In [1]:
# script to compile results of flame speed sensitivity

In [1]:
import os
import sys
import copy
import pickle
import concurrent.futures
import numpy as np
import pandas as pd

import cantera as ct
import rmgpy.chemkin

sys.path.append('/work/westgroup/harris.se/autoscience/autoscience_workflow/workflow/scripts/kinetics')
import kineticfun


import matplotlib.pyplot as plt
%matplotlib inline

In [2]:
# Load the base model
basedir = '/work/westgroup/harris.se/autoscience/autoscience/butane/rmg_model'
# basedir = '/work/westgroup/harris.se/autoscience/autoscience/butane/naive_rmg_model'

base_chemkin = os.path.join(basedir, 'chem_annotated.inp')
dictionary = os.path.join(basedir, 'species_dictionary.txt')
transport = os.path.join(basedir, 'tran.dat')
species_list, reaction_list = rmgpy.chemkin.load_chemkin_file(base_chemkin, dictionary_path=dictionary, transport_path=transport)


438749050.py:8 <module> INFO Thermo file has default temperature range 300.0 to 1000.0 and 1000.0 to 5000.0


In [3]:
base_flame_speed = 0.41552749

In [4]:
flame_speeds = base_flame_speed * np.ones(len(reaction_list))

In [5]:
# load individual flame speed files
results_dir = '/scratch/harris.se/autoscience/local_sensitivity/results/flame_speeds'
for i in range(0, len(reaction_list)):
    result_file = os.path.join(results_dir, f'flame_speed_{i:04}.txt')
    if not os.path.exists(result_file):
        continue
    with open(result_file, 'r') as f:
        result = f.read()
        flame_speeds[i] = result


In [6]:
flame_speeds

array([0.43123798, 0.41552749, 0.41644524, ..., 0.41552749, 0.41552749,
       0.41552749])

In [7]:
# sort the reaction list by difference in flame speed
order = np.arange(0, len(flame_speeds))
fs_diff = np.abs(flame_speeds - base_flame_speed)
most_sensitive = [x for _, x in sorted(zip(fs_diff, order))][::-1]

In [9]:
# print the top reactions


# lookup up manually:
# 87 -> 313
# 77 -> 288
# 34 -> 247

for i in range(0, 500):
    index = most_sensitive[i]
    if index > len(reaction_list):
        index = index - len(reaction_list)
        print(index, '\t', species_list[index])
    else:
        try:
            if reaction_list[index].family != 'H_Abstraction' and \
                reaction_list[index].family != 'Disproportionation' and \
                reaction_list[index].family != 'intra_H_migration' and \
                reaction_list[index].family != 'R_Addition_MultipleBond':
                continue
            print(index, '\t', reaction_list[index], '\t', reaction_list[index].family)
        except AttributeError:
            continue
            print(index, '\t', reaction_list[index], '\t', 'PDEP')

1245 	 O(5) + C2H3(22) <=> OH(15) + C2H2(25) 	 Disproportionation
480 	 OH(15) + CH2(23) <=> O(5) + CH3(18) 	 H_Abstraction
800 	 OH(15) + C4H71-3(190) <=> H2O(8) + C4H6(194) 	 Disproportionation
417 	 OH(15) + SC4H9(183) <=> H2O(8) + C4H8-2(189) 	 Disproportionation
584 	 HO2(16) + C2H3(22) <=> H2O2(17) + C2H2(25) 	 Disproportionation
993 	 O(5) + C4H71-3(190) <=> OH(15) + C4H6(194) 	 Disproportionation
1175 	 H(14) + C4H8-1(188) <=> H2(13) + C4H71-1(192) 	 H_Abstraction
459 	 CH3(18) + SC4H9(183) <=> CH4(10) + C4H8-2(189) 	 Disproportionation
404 	 OH(15) + PC4H9(182) <=> H2O(8) + C4H8-1(188) 	 Disproportionation
458 	 H(14) + SC4H9(183) <=> H2(13) + C4H8-1(188) 	 Disproportionation
213 	 HO2(16) + C2H5(33) <=> H2O2(17) + C2H4(11) 	 Disproportionation
1111 	 CH3O2(45) + C2H5(33) <=> CH3O2H(46) + C2H4(11) 	 Disproportionation
1023 	 O(5) + C4H8-1(188) <=> OH(15) + C4H71-4(191) 	 H_Abstraction
405 	 OH(15) + SC4H9(183) <=> H2O(8) + C4H8-1(188) 	 Disproportionation
410 	 CH3(18) + PC4H9

In [18]:
flame_speeds[78]

0.4174692600031716

In [5]:
for rxn in reaction_list:
    print(rxn.is_forward)

False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
Fals

In [6]:
reaction_list

[LibraryReaction(index=1, reactants=[Species(index=2, label="O2", thermo=NASA(polynomials=[NASAPolynomial(coeffs=[3.53764,-0.00122828,5.36759e-06,-4.93128e-09,1.45955e-12,-1037.99,4.6718], Tmin=(100,'K'), Tmax=(1087.71,'K')), NASAPolynomial(coeffs=[3.16427,0.00169454,-8.00335e-07,1.5903e-10,-1.14891e-14,-1048.45,6.08303], Tmin=(1087.71,'K'), Tmax=(5000,'K'))], Tmin=(100,'K'), Tmax=(5000,'K'), comment="""Thermo library: BurkeH2O2"""), molecule=[Molecule(smiles="[O][O]")], transport_data=TransportData(shapeIndex=1, epsilon=(887.154,'J/mol'), sigma=(3.467,'angstrom'), dipoleMoment=(0,'De'), polarizability=(0,'angstrom^3'), rotrelaxcollnum=0.0, comment="""PrimaryTransportLibrary"""), molecular_weight=(31.9988,'amu')), Species(index=14, label="H", thermo=NASA(polynomials=[NASAPolynomial(coeffs=[2.5,-1.87769e-11,2.35957e-14,-9.62804e-18,1.20728e-21,25472.7,-0.459566], Tmin=(100,'K'), Tmax=(4762.74,'K')), NASAPolynomial(coeffs=[2.87627,-0.00031258,9.73655e-08,-1.34776e-11,6.99516e-16,25110.4,